In [153]:
import pandas as pd
import numpy as np
from nltk.corpus import stopwords
from nltk.tokenize import toktok, sent_tokenize
from nltk.parse import CoreNLPParser
import re
import pickle

In [2]:
tok = toktok.ToktokTokenizer()

In [3]:
pos_tagger = CoreNLPParser(url='http://localhost:9000', tagtype='pos')

In [4]:
ner_tagger = CoreNLPParser(url='http://localhost:9000', tagtype='ner')
#https://github.com/nltk/nltk/wiki/Stanford-CoreNLP-API-in-NLTK

In [6]:
textes_articles_df = pd.read_csv("refined_data/textes_articles_df.csv")
textes_articles_df = textes_articles_df[textes_articles_df["text"].notnull() & (textes_articles_df["media"]!='CNN')]

In [163]:
del textes_articles_df['Unnamed: 0']

In [19]:
# Prétraitement
def pretraitement(article):
    # tokeniser par phrases
    article_sentences = sent_tokenize(article)
    article_ner_tokens = []
    article_pos_tokens = []
    compteur_phrase = 0
    for sentence in article_sentences:
        # Tokeniser
        sentence_tokens = tok.tokenize(sentence)
        # Assembler les entités nommées et colocations
        sentence_ner = ner_tagger.tag(sentence_tokens)
        ner_tokens = [ner_token for ner_token in sentence_ner if ner_token[1] != 'O']
        # Supprimer les classes fermées avec un POS
        sentence_pos = pos_tagger.tag(sentence_tokens)
        pos_tokens = [pos_token for pos_token in sentence_pos if pos_token[1] in ['ADJ','ADV','INTJ','NOUN','PROPN','VERB']]
        # Ajouter à la liste de phrases tokenisées
        article_ner_tokens.append(ner_tokens)
        article_pos_tokens.append(pos_tokens)
        compteur_phrase += 1
    return article_ner_tokens, article_pos_tokens

In [21]:
article_pretraite = [pretraitement(x) for x in list(textes_articles_df["text"])]

In [131]:
def aggreger_ner_tags(article):
    dict_named_entity = {}
    for sentence in article[0]:
        for entity in sentence:
            dict_named_entity[entity] = dict_named_entity.get(entity,0) + 1
    return dict_named_entity

In [132]:
def aggreger_pos_tags(article):
    dict_pos = {}
    for sentence in article[1]:
        for pos in sentence:
            dict_pos[pos] = dict_pos.get(pos,0) + 1
    return dict_pos

In [165]:
textes_articles_df['ner_dict']=[aggreger_ner_tags(article) for article in article_pretraite]
textes_articles_df['pos_dict']=[aggreger_pos_tags(article) for article in article_pretraite]

In [167]:
f = open("pickle/textes_articles_df.pickle","wb")
pickle.dump(textes_articles_df,f)
f.close()